In [ ]:
!pip install nltk

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install emoji

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 353.7/353.7 kB 6.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for emoji: filename=emoji-2.4.0-py2.py3-none-any.whl size=350809 sha256=c9774d83b39f2fad4fb18fcecd378648ad833edaa58b8558f19ffd2c98d9925e
  Stored in directory: /root/.cache/pip/wheels/79/29/1c/234cae4632803c2ba4a76a71a679eb1383cf590775714e2a21
Successfully built emoji


In [ ]:
import pandas as pd

In [ ]:
data = pd.read_csv('/content/drive/MyDrive/T1_Proce/tweets_2022_abril_junio.csv')

In [ ]:
data.head()

id               created_at      screen_name  \
0  1512186166438637582  2022-04-07 21:50:51 UTC      h0l4d4ni3l4   
1  1512186202367045642  2022-04-07 21:51:00 UTC  Claudio70932894   
2  1512186287284924418  2022-04-07 21:51:20 UTC       Cesar_A_RR   
3  1512186335754301446  2022-04-07 21:51:32 UTC      rosmarieher   
4  1512186407841767424  2022-04-07 21:51:49 UTC        GQuelluen   

                                                text  favorite_count  \
0  RT @ValeMirandaCC: Tras casi 50 años del golpe...               0   
1  RT @UTDTrabajoDigno: Mañana jueves a las 18hrs...               0   
2  RT @JaimeGuajardoR: Aquí está el aporte de @te...               0   
3  RT @melnicksergio: la pelotudez no tiene limit...               0   
4  RT @BSepulvedaHales: Ante la circulación de no...               0   

   retweet_count  
0              0  
1              0  
2              0  
3              0  
4              0

# 1. Limpieza de datos.

En esta sección haremos la limpieza de los datos. Lo primero será eliminar los retweets. Podrían mantenerse, pero el tiempo de cómputo aumentaría en un factor cercano a 4 veces el tiempo de ejecución sin los retweets. 

In [ ]:
# Eliminamos los retweets

data['keep'] = data['text'].map(lambda tweet: False if 'RT @' in tweet else True)
data = data[data['keep'] == True].drop(columns='keep')

In [ ]:
data.shape

(1267504, 6)

In [ ]:
data.nunique()

id                1266850
created_at        1119607
screen_name        126314
text              1222451
favorite_count          1
retweet_count           1
dtype: int64

Del resultado anterior podemos deducir varias cosas. Primero, las columnas ```favorite_count```y ```retweet_count``` tienen el mismo valor para todos los registros, por lo que no son significativas para nuestro análisis.

Además podemos deducir la existencia de registros duplicados que analizaremos en detalle a continuación. 

In [ ]:
# Tweets con ID duplicado

data[data.duplicated(subset='id', keep=False)].sort_values('id')

id               created_at     screen_name  \
489822   1510002806274478081  2022-04-01 21:14:58 UTC    JanSeplveda1   
901193   1510002806274478081  2022-04-01 21:14:58 UTC    JanSeplveda1   
708051   1510003200803303425  2022-04-01 21:16:32 UTC  salvandosesolo   
708050   1510003200803303425  2022-04-01 21:16:32 UTC  salvandosesolo   
91244    1510003256113590277  2022-04-01 21:16:45 UTC  salvandosesolo   
...                      ...                      ...             ...   
2442739  1542579282207178752  2022-06-30 18:42:15 UTC     Felipillo10   
2452725  1542648783103590400  2022-06-30 23:18:25 UTC    chefromiguti   
2452726  1542648783103590400  2022-06-30 23:18:25 UTC    chefromiguti   
2655153  1542648787016986624  2022-06-30 23:18:26 UTC    maryquinones   
3012058  1542648787016986624  2022-06-30 23:18:26 UTC    maryquinones   

                                                      text  favorite_count  \
489822                      @Maida_Chacon @RenatoGarinG Xd               0   
901193                      @Maida_Chacon @RenatoGarinG Xd               0   
708051               @danielstingo https://t.co/6dClJrcKw6               0   
708050               @danielstingo https://t.co/6dClJrcKw6               0   
91244                @danielstingo https://t.co/zdabzgngEB               0   
...                                                    ...             ...   
2442739  @Tereib2 @rodrigo_1892 @pablo_t_andres @fernan...               0   
2452725  @tere_marinovic Quién le tiene miedo a ese gua...               0   
2452726  @tere_marinovic Quién le tiene miedo a ese gua...               0   
2655153                   @tere_marinovic Vieja mata cuelo               0   
3012058                   @tere_marinovic Vieja mata cuelo               0   

         retweet_count  
489822               0  
901193               0  
708051               0  
708050               0  
91244                0  
...                ...  
2442739              0  
2452725              0  
2452726              0  
2655153              0  
3012058              0  

[1163 rows x 6 columns]

Para aquellos registros con ID duplicado, parece ser que el contenido de los tweets es el mismo, y la timestamp parece también ser la misma. Para comprobar lo anterior, efectuaremos comparaciones.

In [ ]:
# ¿El contenido de los registros con id duplicado es el mismo?

data[data.duplicated(subset=['id', 'text'])].shape[0] == data[data.duplicated(subset=['id'])].shape[0]

True

In [ ]:
# ¿El timestamp de los registros con id duplicado es el mismo?


data[data.duplicated(subset=['id', 'created_at'])].shape[0] == data[data.duplicated(subset=['id'])].shape[0]


True

In [ ]:
# ¿Los registros con id duplicado provienen siempre del mismo usuario?

data[data.duplicated(subset=['id', 'screen_name'])].shape[0] == data[data.duplicated(subset=['id'])].shape[0]

True

Encontramos entonces que existen registros con valores duplicados simultáneamente en las columnas ```id```, ```screen_name``` y ```text```, que podemos eliminar.

In [ ]:
data.drop_duplicates(subset=['id', 'screen_name', 'created_at'], keep='first', inplace=True)
data.reset_index(drop=True, inplace=True)
data.nunique()

id                1266850
created_at        1119607
screen_name        126314
text              1222451
favorite_count          1
retweet_count           1
dtype: int64

In [ ]:
data.shape

(1266850, 6)

Esto ya tiene mejor aspecto. Ahora cada tweet tiene ```id``` único.

In [ ]:
data.drop(columns=['favorite_count', 'retweet_count'], inplace=True)
data.reset_index(drop=True, inplace=True)
data.head()

id               created_at      screen_name  \
0  1512186668387913732  2022-04-07 21:52:51 UTC      simonlodijo   
1  1512186985850544129  2022-04-07 21:54:07 UTC  MacaSimplemente   
2  1512187189974683661  2022-04-07 21:54:55 UTC  LuisVer75699645   
3  1512187226398076929  2022-04-07 21:55:04 UTC         MITERRED   
4  1512187244248936452  2022-04-07 21:55:08 UTC   piaelizabethvm   

                                                text  
0  @unveranonaranja @ruidosafest @franciscamusic ...  
1  @LaSuRivas @ElisaLoncon @siliconvalle @Valdebe...  
2    @teanval0207 @izkia @arturozunigaj Excelente...  
3           @mcubillossigall https://t.co/gkg5PwbZhZ  
4  @simonlodijo @ruidosafest @franciscamusic @gio...

Ahora, haremos pre-procesamiento necesario para los tweets:

- Eliminar acentos, carácteres especiales y conectores.
- Convertir varios white spaces seguidos en un solo white space.

In [ ]:
def extra_ws_remover(tweet):
  return ' '.join(filter(lambda x: x != ' ', tweet.split(' ')))

In [ ]:
# Función que nos permite extraer los conectores de los tweets.

import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

sw = set(stopwords.words('spanish'))
def stopwords_remover(tweet, sw=sw):  
  return ' '.join(filter(lambda x: x not in sw, tweet.split(' ')))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [ ]:
# Un ejemplo

stopwords_remover(data.loc[30,:]['text'])

'@mdaza_abogado @Jess99041498 Es derecha quiere empatar imposible, partiendo gobierno ladrón indecente tenían.'

In [ ]:
data.loc[30,:]['text']

'@mdaza_abogado @Jess99041498 Es que la derecha quiere empatar y eso será imposible, partiendo por el gobierno ladrón e indecente que tenían.'

In [ ]:
# Funciones que nos permitirán eliminar las tildes y los carácteres especiales.

import re

def accent_remover(tweet):

  to_remov = {'à': 'a', 'á': 'a',
               'é': 'e', 'è': 'e',
               'ì': 'i', 'í': 'i',
               'ò': 'o', 'ó': 'o',
               'ù': 'u', 'ú': 'u'}

  for char in to_remov.keys():
    tweet = re.sub(char, to_remov[char], tweet)
  return tweet  

import string

def only_abc(tweet):
  tweet = tweet.lower()
  filter = list(string.ascii_lowercase) + [str(i) for i in range(0,10)]
  filter.append(' ')
  filter.append('')
  filter.append('ñ')
  tweet = ''.join([c for c in tweet if c in filter])
  return tweet

In [ ]:
import emoji

# Función que nos permitirá eliminar los emojis

def emoji_remover(tweet):
  tweet = emoji.replace_emoji(tweet, '')
  return tweet

In [ ]:
# Función para aplicar todas las funciones de limpieza simultaneamente.

def full_clean(tweet):
  return emoji_remover(only_abc(accent_remover(stopwords_remover(extra_ws_remover(tweet)))))

In [ ]:
data.loc[:, 'text'] = data.loc[:, 'text'].map(lambda tweet: full_clean(tweet))

In [ ]:
# Eliminamos residuos

void = ''
data['keep'] = data['text'].map(lambda x: True if x not in {'', ' '} else False)

In [ ]:
data = data[data['keep'] == True]

In [ ]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1260720 entries, 0 to 1266849
Data columns (total 5 columns):
 #   Column       Non-Null Count    Dtype 
---  ------       --------------    ----- 
 0   id           1260720 non-null  int64 
 1   created_at   1260720 non-null  object
 2   screen_name  1260720 non-null  object
 3   text         1260720 non-null  object
 4   keep         1260720 non-null  bool  
dtypes: bool(1), int64(1), object(3)
memory usage: 49.3+ MB


In [ ]:
data.nunique()

id             1260720
created_at     1114822
screen_name     125815
text           1189970
keep                 1
dtype: int64

In [ ]:
data.drop(columns='keep', inplace=True)

In [ ]:
data.to_csv('/content/drive/MyDrive/T1_Proce/tweets_final.csv', index=False)

In [ ]:
data.index = data.id

In [ ]:
!pip install datasketch

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.7/76.7 kB 2.8 MB/s eta 0:00:00


# 2. Búsqueda de tweets similares.

Para la búsqueda de tweets similares, ocuparemos la librería ```datasketch```, que cuenta con implementaciones para minhashing y LSH. 

En el caso de la implementación de minhashing, esta librería genera las permutaciones de filas necesarias para los ```signatures```haciendo uso de funciones de [Universal Hashing](https://en.wikipedia.org/wiki/Universal_hashing), en particular de la familia de las funciones de hash basadas en aritmética modular. Según se puede observar en el código de esta librería, las funciones de hash implementadas para formar las permutaciones entregan como resultado enteros de hasta 32 bits. 

El número de permutaciones puede ser indicado al momento de instanciar la clase MinHash. En este caso, hemos decidido ocupar 32 permutaciones (el valor por defecto es 128) por razones que responden al tiempo de ejecución. Una mayor cantidad de permutaciones podría (o no) resultar en una mayor accuracy de los elementos candidatos al momento de efectuar el LSH.

Respecto al LSH, este también se encuentra implementado en la librería datasketch. Una de las grandes ventajas de esta implementación es la optimización para determinar el número de bandas y filas por banda que se incluye dentro de los métodos de dicha clase. Nos basta con indicar entonces un valor para el ```threshold``` y los parámetros ```weights```, que determinarán que tanta importancia se le da al FPR (False positive rate) o FNR (False negative rate) al momento de realizar la optimización para encontrar los parámetros de número de bandas y filas por banda.

In [ ]:
# Parámetros

N_PERM = 32
N_SHINGLES = 3
WEIGHTS = (0.3, 0.7)
THRESHOLD = 0.9

In [ ]:
# Para la creación de los k-shingles, ocuparemos la librería nltk, en particular su módulo ngrams.

# Esta implementación fue sugerida por Chat-GPT.

import nltk
from nltk import ngrams

nltk.download('punkt')

def obtener_k_shingles(texto, k):

    # Generar los k-shingles utilizando la función ngrams de NLTK
    k_shingles = set(ngrams(texto, k))
    
    # Convertir los k-shingles en cadenas de texto
    k_shingles = map(lambda shingle: ''.join(shingle), k_shingles)

    return k_shingles

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [ ]:
from datasketch import MinHash, LeanMinHash

minhashes = dict()

def get_update_minhashes(id, data=data, perm=N_PERM, minhashes=minhashes):
  text = data.loc[id, 'text']  
  minhashes[id] = MinHash(num_perm=perm)
  for d in set(obtener_k_shingles(text,N_SHINGLES)):
    minhashes[id].update(d.encode('utf8'))
  minhashes[id] = LeanMinHash(minhashes[id])
  return None

In [ ]:
data['id'].map(lambda id: get_update_minhashes(id))

id
1512186668387913732    None
1512186985850544129    None
1512187189974683661    None
1512187226398076929    None
1512187244248936452    None
                       ... 
1525908559673712640    None
1525981922115358720    None
1526319160849932288    None
1525857323691950080    None
1525910904239321088    None
Name: id, Length: 1260720, dtype: object

In [ ]:
from datasketch import MinHashLSH

# Definimos una función que nos permite implementar la técnica de LSH con distintos threshold.

def get_lsh(minhashes, threshold):

  lsh = MinHashLSH(num_perm=N_PERM, threshold=threshold, weights=WEIGHTS)

  # map(lambda id: lsh.insert(id, minhashes[id]), minhashes.keys())

  for id, hash in minhashes.items():
    lsh.insert(id, hash)

  return lsh

In [ ]:
# Función que nos permite obtener los resultados de similaridad para un threshold dado. 


def get_lsh_results(minhashes, threshold, results):
  
  lsh = get_lsh(minhashes, threshold)    
  for id in minhashes.keys():     
    similar = lsh.query(minhashes[id])
  
    if id in similar:
      similar.remove(id)
    
    if similar != []:
      results[id] = similar     
  return results

In [ ]:
results = dict()

results = get_lsh_results(minhashes, THRESHOLD, results)

In [ ]:
map_dict = dict()
def get_map(row, map_dict=map_dict):
  id = row['id']
  user = row['screen_name']
  map_dict[id] = user
  return None

In [ ]:
data.apply(get_map, axis=1)

id
1512186668387913732    None
1512186985850544129    None
1512187189974683661    None
1512187226398076929    None
1512187244248936452    None
                       ... 
1525908559673712640    None
1525981922115358720    None
1526319160849932288    None
1525857323691950080    None
1525910904239321088    None
Length: 1260720, dtype: object

In [ ]:
from collections import Counter
results = {map_dict[id]: map(lambda x: map_dict[x], filter(lambda x: x != id, results[id])) for id in results.keys()}

In [ ]:
results = {id: list(Counter(results[id]).items()) for id in results.keys()}

In [ ]:
results

{'caseoievski': [('ELMISMOKUFO', 1), ('vtow8', 2), ('apalomerr', 1)],
 'Arnold73020321': [('Arnold73020321', 1)],
 'leonardo1966o': [('serbomu', 1),
  ('osorio_del', 1),
  ('RCAChileUS', 1),
  ('varancib', 14),
  ('cas3500', 2),
  ('TeliasKetty', 1),
  ('JoseAngelR_', 2),
  ('opt64', 1),
  ('corral_s', 3),
  ('cgloriabb', 2),
  ('Minina76120334', 1),
  ('Worges', 6),
  ('mariaynegro', 1),
  ('aleconcha_', 3),
  ('carpire70', 1),
  ('Claudiaxvs', 1),
  ('mptellechea', 3),
  ('GonzaloCaro', 1),
  ('JOCATALAN8', 1),
  ('pablorodriguezs', 1),
  ('JORGE_KATANA', 1),
  ('juanari72798432', 1),
  ('PatriotaChile8', 7),
  ('ItaloRulli', 1),
  ('leonardo1966o', 12),
  ('RamiroCastroC', 1),
  ('pita09443405', 3),
  ('Anastas65109222', 4),
  ('Respirologo', 1),
  ('VeciPreocupado', 1),
  ('Jesus1234561231', 1),
  ('CarlosTemuco_', 1),
  ('CATALIN78333151', 1),
  ('Pupooo_Pablo', 7),
  ('giorgio_vlenti', 1),
  ('Alberto51551332', 1),
  ('Eduardo18735564', 1),
  ('terranova60', 1),
  ('lmbastias', 1

In [ ]:
counts = data['screen_name'].value_counts()
cardinal_dict = {nombre: counts[nombre] for nombre in results.keys()}

In [ ]:
results_relative = {nombre: list(map(lambda user: (user[0], user[1] / cardinal_dict[nombre]), results[nombre])) for nombre in results.keys()}

In [ ]:
results_relative

{'caseoievski': [('ELMISMOKUFO', 0.0136986301369863),
  ('vtow8', 0.0273972602739726),
  ('apalomerr', 0.0136986301369863)],
 'Arnold73020321': [('Arnold73020321', 0.002551020408163265)],
 'leonardo1966o': [('serbomu', 0.002386634844868735),
  ('osorio_del', 0.002386634844868735),
  ('RCAChileUS', 0.002386634844868735),
  ('varancib', 0.03341288782816229),
  ('cas3500', 0.00477326968973747),
  ('TeliasKetty', 0.002386634844868735),
  ('JoseAngelR_', 0.00477326968973747),
  ('opt64', 0.002386634844868735),
  ('corral_s', 0.007159904534606206),
  ('cgloriabb', 0.00477326968973747),
  ('Minina76120334', 0.002386634844868735),
  ('Worges', 0.014319809069212411),
  ('mariaynegro', 0.002386634844868735),
  ('aleconcha_', 0.007159904534606206),
  ('carpire70', 0.002386634844868735),
  ('Claudiaxvs', 0.002386634844868735),
  ('mptellechea', 0.007159904534606206),
  ('GonzaloCaro', 0.002386634844868735),
  ('JOCATALAN8', 0.002386634844868735),
  ('pablorodriguezs', 0.002386634844868735),
  ('JO

In [ ]:
min_tweets = 50
min_relative = 0.5

In [ ]:
first_filter = set(filter(lambda nombre: cardinal_dict[nombre] >= min_tweets, cardinal_dict.keys()))

In [ ]:
second_filter = {nombre: list(filter(lambda items: items[1] >= min_relative, results_relative[nombre])) for nombre in first_filter}

In [ ]:
third_filter = {nombre: list(filter(lambda items: cardinal_dict[items[0]] >= min_tweets, second_filter[nombre])) for nombre in second_filter.keys()}

In [ ]:
final = {nombre: third_filter[nombre] for nombre in filter(lambda nombre: third_filter[nombre] != [], third_filter.keys())}

In [ ]:
final

{'mondini1912': [('crcostag', 1.2264150943396226)],
 'Angelina_temu': [('crcostag', 1.2037037037037037)],
 'RubenGa64271796': [('crcostag', 0.6770833333333334)],
 'msiomara': [('Yari03179415', 0.6415094339622641)],
 'cl_cordova': [('crcostag', 0.9558823529411765)],
 'EspinaGisselle': [('violher2', 0.8545454545454545)],
 'CastTroySch': [('crcostag', 0.5371900826446281)],
 'NaveaCesar': [('Victorborquezs1', 0.7454545454545455)],
 'MARF71688739': [('ClauDePizan', 1.1772151898734178),
  ('Miltonterasss', 2.170886075949367)],
 'JFBC472': [('JFBC472', 0.6329113924050633)],
 'kommander911': [('PatoMonteroT', 0.6268656716417911)],
 'walter8323': [('crcostag', 0.5603448275862069)],
 'pcsandov': [('crcostag', 1.0833333333333333)],
 'ClauDePizan': [('Miltonterasss', 0.765625)],
 'WakeUpEsGratis': [('crcostag', 0.7738095238095238)],
 'Alexand92533328': [('ClauDePizan', 3.576923076923077),
  ('Miltonterasss', 6.596153846153846),
  ('ValeskaPinilla', 0.5576923076923077),
  ('HAL9000r', 0.75)],
 'MIM